In [1]:
import pennylane as qml
from pennylane import qaoa
from pennylane import numpy as np
from matplotlib import pyplot as plt
from qiskit import *
import networkx as nx

# Define the molecule
# N = 3

In [2]:
def generate_qasm(qubits):
    electrons = 2
    charge = 1
    H = qml.PauliZ(0)
    hf_state = qml.qchem.hf_state(electrons, qubits)
    singles, doubles = qml.qchem.excitations(electrons, qubits)
    s_wires, d_wires = qml.qchem.excitations_to_wires(singles, doubles)
    dev = qml.device("qiskit.aer", wires=qubits)
    @qml.qnode(dev)
    def circuit(params, wires, s_wires, d_wires, hf_state):
        qml.UCCSD(params, wires, s_wires, d_wires, hf_state)
        return qml.expval(H)
    np.random.seed(722)
    params = np.random.rand(len(singles) + len(doubles))
    circuit(
        params,
        wires=range(qubits),
        s_wires=s_wires,
        d_wires=d_wires,
        hf_state=hf_state
    )
    # qml.draw_mpl(circuit)(params, wires=range(qubits), s_wires=s_wires, d_wires=d_wires, hf_state=hf_state)
    dev._circuit.qasm(formatted=True, filename="./raw_qasm/vqe_n{}_from_python.qasm".format(qubits))

In [3]:
qubit_list = [4, 6, 8, 16, 24, 28]

In [4]:
from multiprocessing import Pool
with Pool(16) as p:
    result_dicts = p.map(generate_qasm, qubit_list)

OPENQASM 2.0;
include "qelib1.inc";
qreg q[4];
creg c[4];
x q[0];
x q[1];
h q[0];
h q[1];
rx(-pi/2) q[2];
h q[3];
cx q[0],q[1];
cx q[1],q[2];
cx q[2],q[3];
rz(0.10431523979023348) q[3];
cx q[2],q[3];
cx q[1],q[2];
cx q[0],q[1];
h q[0];
h q[1];
rx(pi/2) q[2];
h q[3];
rx(-pi/2) q[0];
h q[1];
rx(-pi/2) q[2];
rx(-pi/2) q[3];
cx q[0],q[1];
cx q[1],q[2];
cx q[2],q[3];
rz(0.10431523979023348) q[3];
cx q[2],q[3];
cx q[1],q[2];
cx q[0],q[1];
rx(pi/2) q[0];
h q[1];
rx(pi/2) q[2];
rx(pi/2) q[3];
h q[0];
rx(-pi/2) q[1];
rx(-pi/2) q[2];
rx(-pi/2) q[3];
cx q[0],q[1];
cx q[1],q[2];
cx q[2],q[3];
rz(0.10431523979023348) q[3];
cx q[2],q[3];
cx q[1],q[2];
cx q[0],q[1];
h q[0];
rx(pi/2) q[1];
rx(pi/2) q[2];
rx(pi/2) q[3];
h q[0];
h q[1];
h q[2];
rx(-pi/2) q[3];
cx q[0],q[1];
cx q[1],q[2];
cx q[2],q[3];
rz(0.10431523979023348) q[3];
cx q[2],q[3];
cx q[1],q[2];
cx q[0],q[1];
h q[0];
h q[1];
h q[2];
rx(pi/2) q[3];
rx(-pi/2) q[0];
h q[1];
h q[2];
h q[3];
cx q[0],q[1];
cx q[1],q[2];
cx q[2],q[3];
rz(-0.104315